<a href="https://colab.research.google.com/github/HugoLopezGon/UFV_Visualizaci-nDeDatos/blob/main/Clase2.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

## Importación de librerías

In [2]:
from google.colab import drive
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import plotly.express as px

## Carga de los datos

### Importación de Datos desde Google Drive

Para trabajar con los datos en Google Colab, primero conectamos Colab a Google Drive, lo cual permite acceder a los archivos almacenados en la unidad. Esta conexión se establece utilizando el comando adecuado para montar Google Drive en una ruta específica dentro del entorno de Colab.

Luego, se procede a leer el archivo CSV que contiene los datos. Para ello, se define la ruta donde está guardado el archivo en Google Drive y se carga en un DataFrame de pandas, permitiendo manipular y analizar los datos de forma eficiente.

Finalmente, para obtener una visión preliminar de los datos, se utiliza un comando que cuenta los valores no nulos en cada columna del DataFrame. Esto proporciona un resumen inicial de los datos cargados y permite identificar posibles valores faltantes.


In [3]:
# Paso 1: Conectar Google Colab a Google Drive
drive.mount('/content/drive')

# Paso 2: Leer el archivo CSV

# Ruta del archivo en Google Drive
file_path = '/content/drive/My Drive/datos_ejercicio_ventas.csv'

# Cargar el CSV en un DataFrame de pandas
df = pd.read_csv(file_path)

# Mostrar las primeras filas del DataFrame
df.count()



Mounted at /content/drive


COUNTRY          18666
SUBBRAND         18666
YEAR             18666
MONTH            18666
SCENARIO         18666
FORECAST         17766
FORECAST_YEAR    17766
AMOUNT           18666
dtype: int64

# Tratamiento de los datos

## Identificación y Conteo de Predicciones vs Valores Reales

La base de datos contiene información tanto de predicciones de ventas como de ventas reales, lo que nos permite analizar cómo las predicciones de inteligencia artificial se comparan con los valores observados. Esta comparación es crucial para evaluar la precisión de las predicciones y detectar tendencias y patrones estacionales.

### Estructura de la Base de Datos

La base de datos está organizada con las siguientes columnas clave:

- **`COUNTRY`**: Indica el país donde se realizó la venta o predicción. Esto es útil para el análisis geográfico y permite observar diferencias regionales en las ventas.
- **`SUBBRAND`**: Marca específica del producto en cuestión. Esto permite filtrar los datos por marca y facilita la evaluación de ventas específicas de cada marca.
- **`YEAR` y `MONTH`**: Representan el año y el mes de la venta o predicción, lo cual es fundamental para analizar la evolución temporal y estacionalidad de las ventas.
- **`SCENARIO`**: Señala si el registro es una predicción (`AI_forecast`) o un valor real (`Actual`). Esta columna es esencial para diferenciar entre datos observados y generados por inteligencia artificial, lo cual resulta fundamental en el análisis de la precisión de las predicciones.
- **`FORECAST`**: Muestra el mes en el que se generó la predicción. Esta columna es relevante únicamente para registros de tipo predicción (`AI_forecast`), ya que permite calcular el horizonte de la predicción (cuánto tiempo antes de la venta real se generó la predicción).
- **`FORECAST_YEAR`**: Año en el que se generó la predicción, de nuevo aplicable solo a registros de predicción.
- **`AMOUNT`**: Cantidad de ventas o predicciones de ventas, que constituye el objetivo de nuestro análisis. Esta variable nos permite ver la magnitud de las ventas y las proyecciones de inteligencia artificial.

### Relación de la Estructura con el Análisis Actual

Dado que estamos interesados en analizar la proporción de predicciones y ventas reales, se hace necesario un primer paso de filtrado basado en la columna `SCENARIO`. Esto nos permite separar las dos categorías (predicciones y valores reales), proporcionando claridad sobre la cantidad de datos en cada una y permitiendo un análisis diferenciado:

1. **Diferenciación de Tipos de Datos**:
   - Al separar predicciones y valores reales, obtenemos una visión clara de cuántos registros corresponden a cada tipo. Esto es crucial para entender la cobertura y equilibrio de los datos, especialmente si necesitamos más valores reales para evaluar la precisión de las predicciones.

2. **Importancia del Conteo**:
   - Contar las predicciones y ventas reales ayuda a verificar que el conjunto de datos tenga suficiente información en ambas categorías para un análisis significativo. Por ejemplo, una proporción muy baja de ventas reales podría indicar un sesgo hacia las predicciones, lo cual afectaría la representatividad de los resultados.

3. **Visualización de la Proporción**:
   - Finalmente, la visualización de la proporción entre predicciones y valores reales facilita la interpretación de la base de datos y permite detectar posibles desequilibrios entre las dos categorías. Esto es útil para validar que el análisis cuenta con datos suficientes en cada tipo y para comunicar claramente la composición de la base de datos.

Este análisis inicial es esencial para preparar la base de datos de modo que se puedan aplicar técnicas más avanzadas de comparación y evaluación entre predicciones y ventas observadas.


In [4]:
# Suponiendo que ya tienes el DataFrame 'df' cargado como antes
# Filtrar los valores de predicciones (AI_forecast) y valores reales (actual)

# Crear DataFrame de predicciones
df_forecast = df[df['SCENARIO'] == 'AI_forecast']

# Crear DataFrame de valores reales
df_actuals = df[df['SCENARIO'] == 'actual']

# Contar el número de predicciones y valores reales
num_forecast = df_forecast.shape[0]
num_actuals = df_actuals.shape[0]

# Crear un DataFrame resumen para la visualización
df_summary = pd.DataFrame({
    'Type': ['AI_forecast', 'Actual'],
    'Count': [num_forecast, num_actuals]
})

# Mostrar el DataFrame resumen
print(df_summary)

# Crear gráfico de barras con Plotly Express
fig = px.bar(df_summary, x='Type', y='Count', title="Proporción de Predicciones (AI_forecast) y Valores Reales (Actual)")
fig.show()



          Type  Count
0  AI_forecast  17766
1       Actual    900


## Cálculo del Horizonte de Predicción

En este análisis, el horizonte de predicción se define como el intervalo de tiempo entre la fecha en que se genera una predicción y la fecha objetivo para la cual se realiza esa predicción. En términos prácticos, calcular el horizonte de predicción nos permite evaluar qué tan anticipada es una predicción respecto a la fecha de venta. Este dato es útil para interpretar la precisión de las predicciones en función del tiempo y proporciona contexto sobre la capacidad de anticipación de las proyecciones realizadas. En el proyecto, esta medida es clave para determinar la fiabilidad de las predicciones a medida que se alejan en el tiempo de la fecha objetivo.

Para este análisis, tomamos un único ejemplo de país y marca específicos para calcular el horizonte de predicción. Esto es posible porque todas las predicciones en la base de datos tienen el mismo horizonte, por lo que calcularlo para una sola variable es suficiente para extrapolarlo a todas las predicciones.

### Explicación del Código para el Cálculo

1. **Filtrado del Conjunto de Datos por País y Marca**:
   - Se comienza filtrando el DataFrame para un país y una marca específicos, en este caso, `'Portugal'` y `'Lipton (L3)'`. Este filtro selecciona únicamente las filas que corresponden a esta combinación de `COUNTRY` y `SUBBRAND`, lo cual permite enfocar el análisis en una muestra representativa y calcular el horizonte de predicción sin tener que trabajar con todo el conjunto de datos.

2. **Verificación del Formato en las Columnas `MONTH` y `YEAR`**:
   - Para asegurar consistencia en el análisis temporal, se verifica que las columnas `MONTH` y `YEAR` estén en formato `int`. Esto permite una manipulación precisa de las fechas y asegura que los valores en estas columnas sean interpretados correctamente en cálculos posteriores.

3. **Aplicación de Condiciones de Filtrado para Predicciones Específicas**:
   - En el conjunto de datos filtrado, se aplican dos condiciones adicionales para aislar los registros específicos de predicción que necesitamos:
     - Primero, se seleccionan las filas donde la columna `FORECAST` tiene el valor `'AI_P02F'`, lo cual indica que se generó una predicción en enero para el mes de febrero.
     - Segundo, se eligen las filas donde el año de predicción, `FORECAST_YEAR`, es `2023.0`. Estas dos condiciones en conjunto seleccionan únicamente los registros que cumplen con la predicción de febrero de 2023 generada en enero.

4. **Conteo del Horizonte de Predicción**:
   - Una vez filtrados los registros que cumplen con ambas condiciones, se cuenta el número de registros resultantes. Este conteo representa el horizonte de predicción para la combinación seleccionada de país y marca y puede aplicarse a todas las predicciones en el conjunto de datos, dado que comparten el mismo horizonte.

Este análisis proporciona una medida clara del horizonte de predicción, la cual se utilizará en las visualizaciones para evaluar las predicciones a lo largo del tiempo y analizar su precisión en función de la distancia entre la fecha de generación y la fecha objetivo.


In [5]:
# Filtrar el DataFrame para un país y una submarca específica (ejemplo: 'USA' y 'COKE')
# Puedes ajustar los valores de 'COUNTRY' y 'SUBBRAND' según sea necesario
df_filtered = df[(df['COUNTRY'] == 'Portugal') & (df['SUBBRAND'] == 'Lipton (L3)')]

# Asegurándonos de que las columnas 'MONTH' y 'YEAR' están en el formato correcto
df_filtered['MONTH'] = df_filtered['MONTH'].astype(int)
df_filtered['YEAR'] = df_filtered['YEAR'].astype(int)






<ipython-input-5-00ddb505f4f3>:6: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

<ipython-input-5-00ddb505f4f3>:7: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [6]:
# Filtrar los registros que cumplan con las dos condiciones:
# 1. 'FORECAST' igual a 'AI_P02F'
# 2. 'FORECAST_YEAR' igual a 2023.0
df_filtered_condition = df_filtered[(df_filtered['FORECAST'] == 'AI_P02F') & (df_filtered['FORECAST_YEAR'] == 2023.0)]

# Contar el número de registros que cumplen con estas condiciones
count_filtered = df_filtered_condition.shape[0]

# Mostrar el resultado del conteo
print(f"El horizonte de la prediccion es: {count_filtered}")


El horizonte de la prediccion es: 18


### Cálculo del Número de Países y Productos Únicos

Este análisis tiene como objetivo obtener la cantidad de países y productos (submarcas) únicos presentes en el conjunto de datos. Estas métricas iniciales ayudan a comprender la variedad y diversidad en la base de datos, así como el alcance geográfico y de productos que abarcan las ventas o predicciones.

#### Explicación del Código para el Cálculo

1. **Cálculo de Países Únicos**:
   - Se calcula el número de países únicos presentes en la columna `COUNTRY` del DataFrame. Esta métrica proporciona una visión de la cobertura geográfica de los datos, permitiendo identificar si el análisis tiene un enfoque global o si está limitado a una cantidad específica de países.

2. **Cálculo de Submarcas Únicas**:
   - Del mismo modo, se obtiene el número de submarcas únicas presentes en la columna `SUBBRAND`. Esto permite conocer la amplitud de la gama de productos considerados en el análisis y nos ayuda a entender la diversidad de marcas incluidas.

#### Utilidad del Análisis

Obtener estos números es fundamental para el contexto del análisis de ventas y predicciones, ya que:

- La cantidad de **países únicos** revela el alcance geográfico y permite realizar comparaciones o segmentaciones basadas en ubicaciones específicas.
- La cantidad de **productos únicos** indica la variedad de marcas o submarcas, permitiendo análisis diferenciados según el producto y facilitando la personalización de predicciones o estrategias de ventas para cada uno.

En conjunto, estos cálculos ofrecen una primera impresión de la cobertura y diversidad de los datos, ayudando a estructurar mejor las visualizaciones y a dirigir el análisis a niveles específicos de país o producto cuando sea necesario.


In [7]:
# Volvemos a calcular el número de países y productos (submarcas) únicos

# Número de países únicos en el archivo
num_paises = df['COUNTRY'].nunique()

# Número de productos (SUBBRAND) únicos en el archivo
num_productos = df['SUBBRAND'].nunique()

num_paises, num_productos

(9, 6)

### Manejo de valores nulos en FORECAST y FORECAST_YEAR

Los valores nulos en las columnas `FORECAST` y `FORECAST_YEAR` ocurren, probablemente, en las ventas reales (cuando `SCENARIO = 'Actual'`), ya que estas filas no requieren una fecha de predicción.

#### Acción:
1. **Rellenar los valores nulos**:
   - Utilizar un marcador específico como `'No Forecast'` en `FORECAST`.
   - Usar `NaN` o `2023` en `FORECAST_YEAR` si tiene sentido en el contexto.

2. **Alternativa**:
   - Eliminar las filas nulas si el análisis solo incluye predicciones.


In [8]:
# Llenar los valores nulos en la columna 'FORECAST'
# Si el valor en 'SCENARIO' es 'Actual', asignamos 'No Forecast' en 'FORECAST'
df['FORECAST'] = df.apply(lambda row: 'No Forecast' if pd.isna(row['FORECAST']) and row['SCENARIO'] == 'Actual' else row['FORECAST'], axis=1)

# Llenar los valores nulos en la columna 'FORECAST_YEAR'
# Si el valor en 'SCENARIO' es 'Actual', asignamos 2023.0 en 'FORECAST_YEAR' (o NaN si prefieres mantener los nulos)
df['FORECAST_YEAR'] = df.apply(lambda row: 2023.0 if pd.isna(row['FORECAST_YEAR']) and row['SCENARIO'] == 'Actual' else row['FORECAST_YEAR'], axis=1)



### Revisión de Valores Negativos en AMOUNT

Dado que `AMOUNT` representa ventas, los valores negativos parecen anómalos y deberían revisarse.

#### Acción:
1. **Filtrar las filas con valores negativos en `AMOUNT`** para determinar si corresponden a errores de carga.
2. **Opciones de manejo**:
   - Eliminar las filas con valores negativos.
   - Cambiar los valores negativos a `0` si realmente representan faltas de ventas o errores.


In [9]:
# Filtrar filas con valores negativos en 'AMOUNT' para revisar
negative_amounts = df[df['AMOUNT'] < 0]
print("Filas con valores negativos en 'AMOUNT':")
print(negative_amounts)

# Opciones para manejar los valores negativos:
# Opción 1: Eliminar filas con valores negativos en 'AMOUNT'
df = df[df['AMOUNT'] >= 0]

Filas con valores negativos en 'AMOUNT':
       COUNTRY     SUBBRAND  YEAR  MONTH SCENARIO FORECAST  FORECAST_YEAR  \
6564   Hungary     7up (L3)  2023      9   actual      NaN            NaN   
7261   Hungary     7up (L3)  2024      1   actual      NaN            NaN   
7904    Norway  Lipton (L3)  2024      7   actual      NaN            NaN   
8791   Hungary     7up (L3)  2023     11   actual      NaN            NaN   
11325  Hungary     7up (L3)  2023      7   actual      NaN            NaN   
11659   Norway  Lipton (L3)  2023      9   actual      NaN            NaN   
14006  Hungary     7up (L3)  2023     12   actual      NaN            NaN   
15840   Norway  Lipton (L3)  2024      3   actual      NaN            NaN   
17174  Hungary     7up (L3)  2024      2   actual      NaN            NaN   
17719   Norway  Lipton (L3)  2024      8   actual      NaN            NaN   

              AMOUNT  
6564   -19481.652378  
7261     -188.474017  
7904    -3177.460145  
8791   -13549.37155

### Uniformidad en Formato de Texto (Mayúsculas/Minúsculas)

Para evitar problemas al filtrar, todas las columnas de texto (`COUNTRY`, `SUBBRAND`, `SCENARIO`, `FORECAST`) deben estar en mayúsculas.

#### Acción:
- Asegurarse de que todas las entradas de texto estén en mayúsculas utilizando `str.upper()`.


In [10]:
# Convertir todas las entradas de texto a mayúsculas en las columnas especificadas
df['COUNTRY'] = df['COUNTRY'].str.upper()
df['SUBBRAND'] = df['SUBBRAND'].str.upper()
df['SCENARIO'] = df['SCENARIO'].str.upper()
df['FORECAST'] = df['FORECAST'].str.upper()


<ipython-input-10-9fe4029cdf6d>:2: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

<ipython-input-10-9fe4029cdf6d>:3: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

<ipython-input-10-9fe4029cdf6d>:4: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

<ipython-input-10-9fe4029

### Validación de Rango de MONTH

La columna `MONTH` debe tener valores en el rango de 1 a 12. Es importante verificar si existen valores fuera de este rango, ya que podrían indicar errores.

#### Acción:
- Filtrar filas con `MONTH` fuera del rango (1-12) y determinar si es necesario corregir o eliminar dichos valores.


In [11]:
# Filtrar filas con valores de 'MONTH' fuera del rango 1-12 para revisar
invalid_months = df[(df['MONTH'] < 1) | (df['MONTH'] > 12)]
print("Filas con valores de 'MONTH' fuera del rango 1-12:")
print(invalid_months)

# Opciones para manejar los valores fuera de rango:
# Opción 1: Eliminar filas con 'MONTH' fuera del rango
#df = df[(df['MONTH'] >= 1) & (df['MONTH'] <= 12)]



Filas con valores de 'MONTH' fuera del rango 1-12:
Empty DataFrame
Columns: [COUNTRY, SUBBRAND, YEAR, MONTH, SCENARIO, FORECAST, FORECAST_YEAR, AMOUNT]
Index: []


### Conversión de Tipos de Datos

Las columnas `YEAR` y `MONTH` deben estar en formato `int` para facilitar el cálculo de fechas y el análisis temporal.

#### Acción:
- Asegurarse de que `YEAR` y `MONTH` estén en formato `int`, realizando la conversión si es necesario.


In [12]:
# Convertir 'YEAR' y 'MONTH' a tipo int si no están ya en ese formato
df['YEAR'] = df['YEAR'].astype(int)
df['MONTH'] = df['MONTH'].astype(int)


## Generación de la Columna de Fecha Completa (`DATE`)

Para facilitar el análisis temporal y mejorar la visualización de tendencias y estacionalidades, es importante disponer de una columna que represente la fecha completa en cada registro. La creación de la columna `DATE` permite obtener una referencia temporal precisa al combinar el año (`YEAR`) y el mes (`MONTH`). Esto convierte los valores separados en una fecha estructurada, facilitando futuras visualizaciones de series de tiempo.

### Explicación del Código para Crear la Columna `DATE`

1. **Conversión de `YEAR` y `MONTH` a Cadena de Texto**:
   - Para crear la columna `DATE`, primero se convierten las columnas `YEAR` y `MONTH` a texto. Esto permite unir ambos valores de forma precisa para generar una fecha válida.

2. **Generación de la Fecha Completa**:
   - Una vez que `YEAR` y `MONTH` están en formato texto, se concatenan con el día "01" para formar una fecha en el formato `YYYY-MM-DD`. El uso del día "01" representa el primer día del mes, permitiendo una interpretación mensual sin necesitar la fecha exacta del día de la venta o predicción.
   
3. **Conversión a Formato de Fecha**:
   - La función `pd.to_datetime` convierte la fecha concatenada en un objeto de tipo `datetime`, lo que permite utilizar esta columna en análisis temporales y visualizaciones de series de tiempo.

### Utilidad de la Columna `DATE`

La columna `DATE` es fundamental para cualquier análisis temporal, ya que permite observar y comparar la evolución de las ventas o predicciones mes a mes. Esta estructura es especialmente útil para analizar tendencias estacionales o cambios a lo largo del tiempo, y facilita el uso de herramientas de visualización para series de tiempo, como gráficos de líneas o áreas.


In [13]:
# Crear la columna 'DATE' combinando 'YEAR' y 'MONTH' para cada registro
df['DATE'] = pd.to_datetime(df['YEAR'].astype(str) + '-' + df['MONTH'].astype(str) + '-01')


## Gráficos exploratorios tras la limpieza

In [14]:
# 1. Visualización de la Distribución de AMOUNT por COUNTRY
fig_country = px.box(df, x='COUNTRY', y='AMOUNT', title="Distribución de Ventas (AMOUNT) por País")
fig_country.show()

In [15]:
# 2. Visualización de la Distribución de AMOUNT por SUBBRAND
fig_subbrand = px.box(df, x='SUBBRAND', y='AMOUNT', title="Distribución de Ventas (AMOUNT) por Marca (SUBBRAND)")
fig_subbrand.show()

## **Visualización de los datos**

##  1. Análisis de Distribución y Comparación por País y Marca

In [16]:
# Gráfico de Barras para Ventas Totales por País (sin diferenciar marca)
fig_sales_by_country = px.bar(
    df,
    x='COUNTRY',
    y='AMOUNT',
    title="Ventas Totales por País",
    labels={'AMOUNT': 'Ventas Totales (AMOUNT)', 'COUNTRY': 'País'},
    color_discrete_sequence=['blue']  # Azul pastel para un aspecto visual suave
)

# Configuración de fondo en blanco
fig_sales_by_country.update_layout(
    plot_bgcolor='white',    # Fondo del gráfico en blanco
    paper_bgcolor='white'    # Fondo del área total en blanco
)

fig_sales_by_country.show()


In [17]:
# Gráfico de Tarta para Ventas Totales por Marca (SUBBRAND)
fig_sales_by_brand_pie = px.pie(
    df,
    names='SUBBRAND',
    values='AMOUNT',
    title="Distribución de Ventas Totales por Marca",
    color='SUBBRAND',  # Colorear cada porción según la marca para consistencia visual
    color_discrete_sequence=['#FFD700', '#A9A9A9', '#90EE90', '#ADD8E6', '#FFB6C1', '#FFA07A']  # Colores pastel para cada marca
)

# Configuración de fondo en blanco
fig_sales_by_brand_pie.update_layout(
    plot_bgcolor='white',    # Fondo del gráfico en blanco
    paper_bgcolor='white'    # Fondo del área total en blanco
)

fig_sales_by_brand_pie.show()


In [18]:
# Definir la secuencia de colores en tonos pastel
color_sequence = ['#FFD700', '#A9A9A9', '#90EE90', '#ADD8E6', '#FFB6C1', '#FFA07A']
# Amarillo pastel, Gris para Pepsi Max, Verde pastel para 7Up, Azul claro, Rojo pastel, y Rosa claro

# Crear el gráfico de barras apilado usando px.histogram con escala logarítmica en el eje y
fig_sales_country_brand = px.histogram(
    df,
    x='COUNTRY',
    y='AMOUNT',
    color='SUBBRAND',
    title="Paso 1: Análisis de Distribución y Comparación por País y Marca - Ventas Totales por País y Marca",
    labels={'AMOUNT': 'Ventas Totales (AMOUNT)', 'COUNTRY': 'País'},
    barmode='stack',  # Modo apilado para visualizar el total de ventas por país y marca
    color_discrete_sequence=color_sequence  # Aplicar secuencia de colores en tonos pastel
)

# Cambiar el fondo a blanco y aplicar escala logarítmica en el eje y
fig_sales_country_brand.update_layout(
    plot_bgcolor='white',    # Fondo del gráfico en blanco
    paper_bgcolor='white',   # Fondo del área total en blanco
    yaxis=dict(type='log')   # Aplicar escala logarítmica en el eje y
)

# Mostrar gráfico
fig_sales_country_brand.show()



## 2. Cual es la tendencia y estacionalidad del país con menos ventas y la marca con más ventas

### Análisis de Tendencias en Series Temporales Usando Media Móvil

Para identificar tendencias en una serie temporal, especialmente cuando se busca analizar el crecimiento o decrecimiento de una variable a lo largo del tiempo, la media móvil es una herramienta útil. En este análisis, utilizamos una media móvil de 3 meses para suavizar las ventas mensuales, permitiéndonos observar la tendencia subyacente al eliminar las variaciones de corto plazo.

#### Concepto de Media Móvil

La **media móvil** es un método estadístico que calcula el promedio de un conjunto de datos en un intervalo de tiempo determinado. En una serie temporal, la media móvil ayuda a suavizar fluctuaciones al promediar los valores de la variable en periodos consecutivos. Al reducir el “ruido” de las variaciones de corto plazo, la media móvil permite observar una **tendencia general** en los datos.

En este caso, usamos una **media móvil de 3 meses**:
- La media móvil de 3 meses toma el promedio de las ventas de un mes junto con las de los dos meses anteriores.
- Esto ayuda a reducir la volatilidad de los datos, proporcionando una curva de tendencia más suave que representa mejor la dirección de las ventas.

#### Desarrollo de la Serie Temporal con Media Móvil

1. **Agrupación Mensual**: Primero, agrupamos las ventas a nivel mensual. Esto garantiza que cada mes tenga un solo valor de ventas, lo cual es esencial para un análisis de series temporales de forma continua.

2. **Cálculo de la Media Móvil de 3 Meses**: Después de agrupar los datos, calculamos la media móvil usando una ventana de 3 meses. Esto se realiza mediante la función `.rolling(window=3).mean()`, que calcula el promedio de cada mes con los dos meses anteriores, generando una columna `MEDIA_MOVIL_3_MESES` en el DataFrame.

3. **Visualización de la Serie Temporal**: En el gráfico de series temporales, se incluyen dos líneas:
   - **Ventas Mensuales**: Representa las ventas reales de cada mes. Esto muestra las fluctuaciones específicas y estacionalidades, permitiendo ver los aumentos y caídas en ventas.
   - **Media Móvil de 3 Meses**: Representa la tendencia suavizada de las ventas mensuales. La línea de media móvil revela la tendencia general (crecimiento o decrecimiento) en ventas, eliminando las variaciones mensuales que podrían ser causadas por factores estacionales o de corto plazo.




**País con menos ventas**

In [24]:
# Identificar el país con menos ventas
country_least_sales = df.groupby('COUNTRY')['AMOUNT'].sum().idxmin()

# Filtrar los datos para el país con menos ventas
df_country_least_sales = df[df['COUNTRY'] == country_least_sales]

# Filtrar solo los datos reales para el país con menos ventas
df_country_least_sales_actual = df[(df['COUNTRY'] == country_least_sales) & (df['SCENARIO'] == 'ACTUAL')]

# Agrupar por año y mes para obtener la venta total real por mes
df_country_least_sales_actual = df_country_least_sales_actual.groupby(['YEAR', 'MONTH']).agg({'AMOUNT': 'sum'}).reset_index()

# Crear la columna de fecha completa en nivel mensual
df_country_least_sales_actual['DATE'] = pd.to_datetime(df_country_least_sales_actual[['YEAR', 'MONTH']].assign(DAY=1))

# Ordenar por fecha
df_country_least_sales = df_country_least_sales_actual.sort_values(by='DATE')

# Calcular la media móvil de 3 meses sobre los valores reales
df_country_least_sales['MEDIA_MOVIL_3_MESES'] = df_country_least_sales_actual['AMOUNT'].rolling(window=3).mean()


In [26]:
import plotly.graph_objects as go
import plotly.express as px
import plotly.graph_objects as go
from statsmodels.tsa.seasonal import seasonal_decompose
# Crear la figura de Plotly
fig = go.Figure()

# Agregar la serie de ventas mensuales
fig.add_trace(go.Scatter(
    x=df_country_least_sales['DATE'],
    y=df_country_least_sales['AMOUNT'],
    mode='lines',
    name='Ventas Mensuales',
    line=dict(color='#ADD8E6')  # Azul pastel
))

# Agregar la serie de media móvil de 3 meses
fig.add_trace(go.Scatter(
    x=df_country_least_sales['DATE'],
    y=df_country_least_sales['MEDIA_MOVIL_3_MESES'],
    mode='lines',
    name='Tendencia',
    line=dict(color='#FF4500', width=2.5)  # Naranja oscuro
))

# Configuración del gráfico
fig.update_layout(
    title=f"Tendencia de Ventas en el País con Menos Ventas ({country_least_sales}) - Media Móvil 3 Meses",
    xaxis=dict(title="Fecha", dtick="M1", tickformat="%b %Y"),
    yaxis=dict(title="Ventas (AMOUNT)"),
    plot_bgcolor='white',
    paper_bgcolor='white'
)

fig.show()

# Realizar la descomposición de la serie temporal
decomposition = seasonal_decompose(df_country_least_sales['AMOUNT'], model='additive', period=6)

# Crear un DataFrame con el componente de estacionalidad
df_estacionalidad = pd.DataFrame({
    'Fecha': decomposition.seasonal.index,
    'Estacionalidad': decomposition.seasonal
}).reset_index(drop=True)

# Crear la figura de estacionalidad
fig_estacionalidad = px.line(df_estacionalidad, x='Fecha', y='Estacionalidad', title="Componente de Estacionalidad")

# Configuración de la visualización
fig_estacionalidad.update_layout(
    xaxis_title="Fecha",
    yaxis_title="Estacionalidad",
    template="plotly_white"
)

# Mostrar gráfico
fig_estacionalidad.show()

**Marca con más ventas**

In [27]:
# Filtrar solo los valores "actuals" (reales) para la serie temporal
df_actuals = df[df['SCENARIO'] == 'ACTUAL']

# Identificar la marca con más ventas entre los valores reales
brand_most_sales = df_actuals.groupby('SUBBRAND')['AMOUNT'].sum().idxmax()

# Filtrar los datos para la marca con más ventas usando solo datos reales
df_brand_most_sales = df_actuals[df_actuals['SUBBRAND'] == brand_most_sales]

# Agrupar por año y mes para obtener la venta total por mes
df_brand_most_sales = df_brand_most_sales.groupby(['YEAR', 'MONTH']).agg({'AMOUNT': 'sum'}).reset_index()

# Crear la columna de fecha completa en nivel mensual
df_brand_most_sales['DATE'] = pd.to_datetime(df_brand_most_sales[['YEAR', 'MONTH']].assign(DAY=1))

# Ordenar por fecha
df_brand_most_sales = df_brand_most_sales.sort_values(by='DATE')

# Calcular la media móvil de 3 meses
df_brand_most_sales['MEDIA_MOVIL_3_MESES'] = df_brand_most_sales['AMOUNT'].rolling(window=3).mean()

# Verificar el resultado
print(df_brand_most_sales.head())


   YEAR  MONTH        AMOUNT       DATE  MEDIA_MOVIL_3_MESES
0  2023      1  1.485655e+07 2023-01-01                  NaN
1  2023      2  1.546332e+07 2023-02-01                  NaN
2  2023      3  2.087355e+07 2023-03-01         1.706447e+07
3  2023      4  1.793494e+07 2023-04-01         1.809060e+07
4  2023      5  2.232545e+07 2023-05-01         2.037798e+07


In [ ]:
# Usaremos la marca con más ventas
# Identificar la marca con más ventas
brand_most_sales = df.groupby('SUBBRAND')['AMOUNT'].sum().idxmax()

# Filtrar los datos para la marca con más ventas
df_brand_most_sales = df[df['SUBBRAND'] == brand_most_sales]

# Agrupar por año y mes para obtener la venta total por mes
df_brand_most_sales = df_brand_most_sales.groupby(['YEAR', 'MONTH']).agg({'AMOUNT': 'sum'}).reset_index()

# Crear la columna de fecha completa en nivel mensual
df_brand_most_sales['DATE'] = pd.to_datetime(df_brand_most_sales[['YEAR', 'MONTH']].assign(DAY=1))

# Ordenar por fecha
df_brand_most_sales = df_brand_most_sales.sort_values(by='DATE')

# Calcular la media móvil de 3 meses
df_brand_most_sales['MEDIA_MOVIL_3_MESES'] = df_brand_most_sales['AMOUNT'].rolling(window=3).mean()


In [29]:
import plotly.graph_objects as go
import plotly.express as px
import plotly.graph_objects as go
from statsmodels.tsa.seasonal import seasonal_decompose


# Crear la figura de Plotly
fig = go.Figure()

# Agregar la serie de ventas mensuales
fig.add_trace(go.Scatter(
    x=df_brand_most_sales['DATE'],
    y=df_brand_most_sales['AMOUNT'],
    mode='lines',
    name='Ventas Mensuales',
    line=dict(color='#ADD8E6')  # Azul pastel
))

# Agregar la serie de media móvil de 3 meses
fig.add_trace(go.Scatter(
    x=df_brand_most_sales['DATE'],
    y=df_brand_most_sales['MEDIA_MOVIL_3_MESES'],
    mode='lines',
    name='Tendencia',
    line=dict(color='#FF4500', width=2.5)  # Naranja oscuro
))

# Configuración del gráfico
fig.update_layout(
    title=f"Tendencia de Ventas para la Marca con Más Ventas ({brand_most_sales}) - Media Móvil 3 Meses",
    xaxis=dict(title="Fecha", dtick="M1", tickformat="%b %Y"),
    yaxis=dict(title="Ventas (AMOUNT)"),
    plot_bgcolor='white',
    paper_bgcolor='white'
)

fig.show()
# Realizar la descomposición de la serie temporal
decomposition = seasonal_decompose(df_brand_most_sales['AMOUNT'], model='additive', period=6)

# Crear un DataFrame con el componente de estacionalidad
df_estacionalidad = pd.DataFrame({
    'Fecha': decomposition.seasonal.index,
    'Estacionalidad': decomposition.seasonal
}).reset_index(drop=True)

# Crear la figura de estacionalidad
fig_estacionalidad = px.line(df_estacionalidad, x='Fecha', y='Estacionalidad', title="Componente de Estacionalidad")

# Configuración de la visualización
fig_estacionalidad.update_layout(
    xaxis_title="Fecha",
    yaxis_title="Estacionalidad",
    template="plotly_white"
)

# Mostrar gráfico
fig_estacionalidad.show()


## 3. Cuales son las predicciones hechas en España y como de buenas son.


In [30]:
import re

# Extraer el mes de la predicción si el formato es correcto, y manejar valores que no coincidan
df['MES_PREDICCION'] = df['FORECAST'].apply(lambda x: int(re.search(r'AI_P(\d{2})', x).group(1)) - 1 if pd.notnull(x) and re.search(r'AI_P(\d{2})', x) else None)

# Verificar el resultado
print(df[['FORECAST', 'MES_PREDICCION']].head())


  FORECAST  MES_PREDICCION
0  AI_P02F             1.0
1  AI_P10F             9.0
2  AI_P09F             8.0
3  AI_P10F             9.0
4  AI_P03F             2.0


In [31]:
# Crear columna de fecha de inicio de la predicción, manejando valores nulos
df['FECHA_INICIO_PREDICCION'] = df.apply(
    lambda row: pd.Timestamp(year=int(row['FORECAST_YEAR']), month=int(row['MES_PREDICCION']), day=1)
    if pd.notnull(row['FORECAST_YEAR']) and pd.notnull(row['MES_PREDICCION']) else pd.NaT,
    axis=1
)

# Crear columna de fecha objetivo de la predicción
df['FECHA_OBJETIVO'] = pd.to_datetime(df[['YEAR', 'MONTH']].assign(DAY=1))

# Calcular el horizonte en meses solo para las filas sin nulos en FECHA_INICIO_PREDICCION o FECHA_OBJETIVO
df['HORIZONTE'] = df.apply(
    lambda row: (row['FECHA_OBJETIVO'].year - row['FECHA_INICIO_PREDICCION'].year) * 12 + (row['FECHA_OBJETIVO'].month - row['FECHA_INICIO_PREDICCION'].month)
    if pd.notnull(row['FECHA_INICIO_PREDICCION']) and pd.notnull(row['FECHA_OBJETIVO']) else None,
    axis=1
)

# Verificar el resultado
print(df.head())


         COUNTRY        SUBBRAND  YEAR  MONTH     SCENARIO FORECAST  \
0       PORTUGAL     LIPTON (L3)  2023     12  AI_FORECAST  AI_P02F   
1  GREAT BRITAIN     LIPTON (L3)  2023     12  AI_FORECAST  AI_P10F   
2          SPAIN  PEPSI MAX (L3)  2023     12  AI_FORECAST  AI_P09F   
3  GREAT BRITAIN        7UP (L3)  2024     12  AI_FORECAST  AI_P10F   
4        HUNGARY     LIPTON (L3)  2023      9  AI_FORECAST  AI_P03F   

   FORECAST_YEAR         AMOUNT       DATE  MES_PREDICCION  \
0         2023.0  754356.237194 2023-12-01             1.0   
1         2023.0  560030.558029 2023-12-01             9.0   
2         2023.0   88501.980847 2023-12-01             8.0   
3         2023.0  363224.511516 2024-12-01             9.0   
4         2023.0  396176.120491 2023-09-01             2.0   

  FECHA_INICIO_PREDICCION FECHA_OBJETIVO  HORIZONTE  
0              2023-01-01     2023-12-01       11.0  
1              2023-09-01     2023-12-01        3.0  
2              2023-08-01     2023-12-

In [32]:
# Filtrar el DataFrame para obtener solo las predicciones ('AI_FORECAST') y valores reales ('ACTUAL')
df_predicciones = df[df['SCENARIO'] == 'AI_FORECAST']
df_reales = df[df['SCENARIO'] == 'ACTUAL'][['COUNTRY', 'SUBBRAND', 'DATE', 'AMOUNT']]

# Renombrar DATE a FECHA_OBJETIVO en los valores reales para que coincida con las predicciones
df_reales.rename(columns={'DATE': 'FECHA_OBJETIVO', 'AMOUNT': 'VALOR_ACTUAL'}, inplace=True)

# Unir las predicciones con los valores reales basándonos en FECHA_OBJETIVO, COUNTRY y SUBBRAND
df_predicciones = df_predicciones.merge(
    df_reales,
    on=['COUNTRY', 'SUBBRAND', 'FECHA_OBJETIVO'],
    how='left'
)

# Calcular la diferencia entre la predicción y el valor actual (error de predicción)
df_predicciones['ERROR_PREDICCION'] = df_predicciones['AMOUNT'] - df_predicciones['VALOR_ACTUAL']

# Verificar el resultado de las primeras filas después de corregir el filtro
df_predicciones[['COUNTRY', 'SUBBRAND', 'YEAR', 'MONTH', 'SCENARIO', 'FORECAST', 'FECHA_OBJETIVO', 'AMOUNT', 'VALOR_ACTUAL', 'ERROR_PREDICCION']].head()



COUNTRY        SUBBRAND  YEAR  MONTH     SCENARIO FORECAST  \
0       PORTUGAL     LIPTON (L3)  2023     12  AI_FORECAST  AI_P02F   
1  GREAT BRITAIN     LIPTON (L3)  2023     12  AI_FORECAST  AI_P10F   
2          SPAIN  PEPSI MAX (L3)  2023     12  AI_FORECAST  AI_P09F   
3  GREAT BRITAIN        7UP (L3)  2024     12  AI_FORECAST  AI_P10F   
4        HUNGARY     LIPTON (L3)  2023      9  AI_FORECAST  AI_P03F   

  FECHA_OBJETIVO         AMOUNT   VALOR_ACTUAL  ERROR_PREDICCION  
0     2023-12-01  754356.237194  596053.776708     158302.460486  
1     2023-12-01  560030.558029  533035.699598      26994.858431  
2     2023-12-01   88501.980847  105442.112234     -16940.131387  
3     2024-12-01  363224.511516            NaN               NaN  
4     2023-09-01  396176.120491  316922.252436      79253.868055

In [33]:
# Calcular el error absoluto de cada predicción
df_predicciones['ERROR_ABSOLUTO'] = abs(df_predicciones['ERROR_PREDICCION'])

# Eliminar filas con valores nulos en ERROR_ABSOLUTO
df_predicciones_limpio = df_predicciones.dropna(subset=['ERROR_ABSOLUTO'])


In [34]:
import pandas as pd

# Filtrar el DataFrame para obtener solo las predicciones en España
df_predicciones_espana = df_predicciones_limpio[df_predicciones_limpio['COUNTRY'] == 'SPAIN']

# Agrupar por horizonte y calcular el error absoluto medio y desviación estándar del error
df_error_promedio_espana = df_predicciones_espana.groupby('HORIZONTE').agg(
    ERROR_MEDIO=('ERROR_ABSOLUTO', 'mean'),      # Promedio de error absoluto
    ERROR_STD=('ERROR_ABSOLUTO', 'std')          # Desviación estándar del error
).reset_index()



In [35]:
import plotly.graph_objects as go
import pandas as pd

# Calcular percentiles del error absoluto
df_percentiles = df_predicciones_espana.groupby('HORIZONTE')['ERROR_ABSOLUTO'].quantile([0.25, 0.5, 0.75]).unstack()
df_percentiles.columns = ['PERCENTIL_25', 'MEDIANA', 'PERCENTIL_75']
df_percentiles.reset_index(inplace=True)

# Crear la figura base
fig = go.Figure()

# Añadir la banda de sombra para el percentil 25-75
fig.add_trace(go.Scatter(
    x=df_percentiles['HORIZONTE'],
    y=df_percentiles['PERCENTIL_75'],
    mode='lines',
    line=dict(width=0),
    showlegend=False,
    hoverinfo='skip'
))

fig.add_trace(go.Scatter(
    x=df_percentiles['HORIZONTE'],
    y=df_percentiles['PERCENTIL_25'],
    mode='lines',
    line=dict(width=0),
    fill='tonexty',  # Rellena el área entre PERCENTIL_75 y PERCENTIL_25
    fillcolor='rgba(0, 176, 246, 0.2)',  # Color de la sombra
    showlegend=False,
    hoverinfo='skip'
))

# Añadir la línea de error absoluto medio con descripción adicional para la sombra azul
fig.add_trace(go.Scatter(
    x=df_error_promedio_espana['HORIZONTE'],
    y=df_error_promedio_espana['ERROR_MEDIO'],
    mode='lines',
    line=dict(color='royalblue', width=2),
    name='Error Absoluto Medio (con Sombra de Variabilidad entre Percentiles 25-75)'  # Descripción completa en la leyenda
))


# Configuración final del gráfico
fig.update_layout(
    title="Precisión de las Predicciones en España en Función del Horizonte con Sombra de Desviación",
    xaxis_title="Horizonte de Predicción (meses)",
    yaxis_title="Error Absoluto",
    template="plotly_white"
)

# Mostrar gráfico
fig.show()


In [40]:
import plotly.express as px

# Filtrar las predicciones con horizonte de predicción igual a 1
df_horizon_1 = df_predicciones_limpio[df_predicciones_limpio['HORIZONTE'] == 1]

# Calcular el error de predicción (en este caso, la diferencia entre el valor real y el predicho)
df_horizon_1['ERROR'] = df_horizon_1['AMOUNT'] - df_horizon_1['VALOR_ACTUAL']



<ipython-input-40-fe9b1f82e742>:7: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [41]:
import plotly.express as px
import plotly.graph_objects as go

# Crear el diagrama de violín sin la nube de puntos
fig = px.violin(df_horizon_1, y='ERROR', box=True, points=None,
                title="Distribución del Error de Predicciones con Horizonte 1 (EL ERROR DEBE DE SER MINIMO)",
                color_discrete_sequence=['rgba(0, 100, 200, 0.6)'])  # Color con transparencia

# Añadir la media del error
fig.add_trace(go.Scatter(
    y=[df_horizon_1['ERROR'].mean()],  # Media del error
    mode="markers+text",
    name="Media",
    text=["Media"],
    textposition="bottom center",
    marker=dict(color="red", size=10),
    showlegend=True
))

# Limitar el rango del eje y si es necesario
fig.update_yaxes(range=[-500000, 500000])

# Mostrar el gráfico
fig.show()


In [51]:
import plotly.express as px

# Crear el gráfico de dispersión
fig = px.scatter(df_predicciones_limpio,
                 x='VALOR_ACTUAL',
                 y='AMOUNT',
                 title="Gráfico de Dispersión: Predicción vs Valor Real",
                 labels={'VALOR_ACTUAL': 'Valor Real', 'AMOUNT': 'Predicción'})

# Añadir la línea de referencia (Predicción = Valor Real)
fig.add_shape(
    type='line',
    x0=0, y0=0,
    x1=max(df_predicciones_limpio['VALOR_ACTUAL']),
    y1=max(df_predicciones_limpio['VALOR_ACTUAL']),
    line=dict(color='Red', dash='dash'),
    xref='x', yref='y',
    name="Línea de referencia (Predicción = Valor Real)"  # Etiqueta para la línea
)

# Añadir anotación en la leyenda para la línea de referencia
fig.add_trace(go.Scatter(
    x=[None], y=[None],
    mode='lines',
    line=dict(color='Red', dash='dash'),
    showlegend=True,
    name='Línea de referencia (Predicción = Valor Real)'
))

# Mostrar el gráfico
fig.show()

